In [0]:
from pyspark.sql.functions import col, rand

In [0]:
%sql
SHOW DATABASES

databaseName default

In [0]:
%sql
SHOW TABLES

database tableName isTemporary default countries false default flights_data false default happiness_scores false default loan_data false default loan_data_females_under_30 false default olympics false default partitioned_loan_data_females_under_30 false

In [0]:
# let's generate a huge dataset with customer IDs
customer_id = spark.range(1, 15000000, 1, 15)

display(customer_id)

id 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 101 102 103 104 105 106 107 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233 234 235 236 237 238 239 240 241 242 243 244 245 246 247 248 249 250 251 252 253 254 255 256 257 258 259 260 261 262 263 264 265 266 267 268 269 270 271 272 273 274 275 276 277 278 279 280 281 282 283 284 285 286 287 288 289 290 291 292 293 294 295 296 297 298 299 300 301 302 303 304 305 306 307 308 309 310 311 312 313 314 315 316 317 318 319 320 321 322 323 324 325 326 327 328 329 330 331 332 333 334 335 336 337 338 339 340 341 342 343 344 345 346 347 348 349 350 351 352 353 354 355 356 357 358 359 360 361 362 363 364 365 366 367 368 369 370 371 372 373 374 375 376 377 378 379 380 381 382 383 384 385 386 387 388 389 390 391 392 393 394 395 396 397 398 399 400 401 402 403 404 405 406 407 408 409 410 411 412 413 414 415 416 417 418 419 420 421 422 423 424 425 426 427 428 429 430 431 432 433 434 435 436 437 438 439 440 441 442 443 444 445 446 447 448 449 450 451 452 453 454 455 456 457 458 459 460 461 462 463 464 465 466 467 468 469 470 471 472 473 474 475 476 477 478 479 480 481 482 483 484 485 486 487 488 489 490 491 492 493 494 495 496 497 498 499 500 501 502 503 504 505 506 507 508 509 510 511 512 513 514 515 516 517 518 519 520 521 522 523 524 525 526 527 528 529 530 531 532 533 534 535 536 537 538 539 540 541 542 543 544 545 546 547 548 549 550 551 552 553 554 555 556 557 558 559 560 561 562 563 564 565 566 567 568 569 570 571 572 573 574 575 576 577 578 579 580 581 582 583 584 585 586 587 588 589 590 591 592 593 594 595 596 597 598 599 600 601 602 603 604 605 606 607 608 609 610 611 612 613 614 615 616 617 618 619 620 621 622 623 624 625 626 627 628 629 630 631 632 633 634 635 636 637 638 639 640 641 642 643 644 645 646 647 648 649 650 651 652 653 654 655 656 657 658 659 660 661 662 663 664 665 666 667 668 669 670 671 672 673 674 675 676 677 678 679 680 681 682 683 684 685 686 687 688 689 690 691 692 693 694 695 696 697 698 699 700 701 702 703 704 705 706 707 708 709 710 711 712 713 714 715 716 717 718 719 720 721 722 723 724 725 726 727 728 729 730 731 732 733 734 735 736 737 738 739 740 741 742 743 744 745 746 747 748 749 750 751 752 753 754 755 756 757 758 759 760 761 762 763 764 765 766 767 768 769 770 771 772 773 774 775 776 777 778 779 780 781 782 783 784 785 786 787 788 789 790 791 792 793 794 795 796 797 798 799 800 801 802 803 804 805 806 807 808 809 810 811 812 813 814 815 816 817 818 819 820 821 822 823 824 825 826 827 828 829 830 831 832 833 834 835 836 837 838 839 840 841 842 843 844 845 846 847 848 849 850 851 852 853 854 855 856 857 858 859 860 861 862 863 864 865 866 867 868 869 870 871 872 873 874 875 876 877 878 879 880 881 882 883 884 885 886 887 888 889 890 891 892 893 894 895 896 897 898 899 900 901 902 903 904 905 906 907 908 909 910 911 912 913 914 915 916 917 918 919 920 921 922 923 924 925 926 927 928 929 930 931 932 933 934 935 936 937 938 939 940 941 942 943 944 945 946 947 948 949 950 951 952 953 954 955 956 957 958 959 960 961 962 963 964 965 966 967 968 969 970 971 972 973 974 975 976 977 978 979 980 981 982 983 984 985 986 987 988 989 990 991 992 993 994 995 996 997 998 999 1000 1001 1002 1003 1004 1005 1006 1007 1008 1009 1010 1011 1012 1013 1014 1015 1016 1017 1018 1019 1020 1021

In [0]:
# we'll generate a dataset with 2 columns: id and percentage (yield on client)
pct_invest_2019 = customer_id.select(col("id").alias("customer_id"), rand(1).alias("pct_investment_2019"))

display(pct_invest_2019)

customer_id pct_investment_2019 1 0.6363787615254752 2 0.5993846534021868 3 0.134842710012538 4 0.07684163905460906 5 0.8539211111755448 6 0.7167704217972344 7 0.24739024075979754 8 0.13674507418513693 9 0.3869569887491171 10 0.6051540605040805 11 0.5513078894057816 12 0.1452399817642237 13 0.26163926627619905 14 0.8530140462553923 15 0.8090257953622899 16 0.9643107647469807 17 0.7312153295256995 18 0.950696177240955 19 0.05412576088744092 20 0.5981412057936335 21 0.05889803594642207 22 0.47822225238918004 23 0.22263323238128896 24 0.34144885513422507 25 0.09037005146045207 26 0.5486344061553862 27 0.44220951468656255 28 0.5331801207037167 29 0.10954865740925235 30 0.8707943287939354 31 0.2145216454861799 32 0.6203802379933062 33 0.9679995204008195 34 0.9762538138976666 35 0.5012667094512947 36 0.7858405823101561 37 0.22696070858457196 38 0.4258104850284544 39 0.3086279543419794 40 0.7735860875700268 41 0.36750147581363635 42 0.6745138064041893 43 0.8107766894849062 44 0.7834393789130706 45 0.9372061757729347 46 0.11989724011471636 47 0.671181909238684 48 0.6712869536921918 49 0.6700570630610045 50 0.5146328663495794 51 0.08314053650034625 52 0.8236079431942233 53 0.2835289872305926 54 0.6468590051259542 55 0.8028217771912095 56 0.10863131103905432 57 0.15043477778272318 58 0.40753015226645095 59 0.9195898134653623 60 0.35202319850909647 61 0.06058579398704933 62 0.14501327237315953 63 0.2970280250906274 64 0.3992368306476186 65 0.18424077073270828 66 0.9786707282126421 67 0.19506920380756332 68 0.5856762737099224 69 0.681517782277308 70 0.2519628438595569 71 0.7714568534199028 72 0.6429968615441546 73 0.5404448590689082 74 0.14811883126643355 75 0.9044642012602166 76 0.8399158806773596 77 0.18566206556985954 78 0.3175971342128566 79 0.22003136723189698 80 0.10019565652162143 81 0.5739892994704174 82 0.24638119692496663 83 0.22088542864599903 84 0.8591410691532463 85 0.8890363414935293 86 0.11580523400567677 87 0.784915783949459 88 0.023149496765865196 89 0.9137170766624237 90 0.2602840975906008 91 0.5916450223016985 92 0.15752545548909225 93 0.8176384469253976 94 0.19275652671515497 95 0.13924112497827423 96 0.3840788240439137 97 0.29119274294353115 98 0.39256162236420145 99 0.2132986201116427 100 0.00372731261484216 101 0.0028016378800466146 102 0.46813862769089776 103 0.6116519197334973 104 0.37782666820382993 105 0.3081620800161492 106 0.5594735116926138 107 0.22875073321217942 108 0.1291186949176638 109 0.3923560383360045 110 0.40016739427411696 111 0.5003811246515943 112 0.3015064109964919 113 0.806913268563875 114 0.14562615827986314 115 0.5583576809617101 116 0.6660895916877052 117 0.47991486693847984 118 0.2799075004229643 119 0.41845451753804186 120 0.7811135679421796 121 0.41552927204433465 122 0.19434614422873364 123 0.06444107879131655 124 0.7384900835583414 125 0.5669578069546074 126 0.5855310086409513 127 0.5757774320948101 128 0.9183693664894321 129 0.7973836076637166 130 0.942723722436596 131 0.5217811927358862 132 0.8756828230002456 133 0.27130884652146126 134 0.5740559328244694 135 0.8717960274208802 136 0.48347746325587193 137 0.4386030216645338 138 0.09921348504859373 139 0.7280438356414382 140 0.9556260081869982 141 0.780428876347643 142 0.520366701905721 143 0.26444615760216195 144 0.2090122801209341 145 0.3620553465531904 146 0.03465158333546592 147 0.032267281596734976 148 0.7218504473666008 149 0.7022700546969574 150 0.16199875931157004 151 0.32628236401906385 152 0.9259281776679887 153 0.19669646862634127 154 0.6148989175660067 155 0.1891756270970124 156 0.6191704874545965 157 0.02014200137561939 158 0.44644823608949624 159 0.7249919862101719 160 0.12395637364903878 161 0.8338611295801245 162 0.07146321241545994 163 0.5427676535722059 164 0.8098004307083576 165 0.9362798443380381 166 0.9529183145559345 167 0.8075413006657625 168 0.1761236600264039 169 0.6918444205972575 170 0.06326343732367057 171 0.6121460092289338 172 0.27554446837290103 173 0.05904697073793719 174 0.8428840222192864 175 0.47269153

In [0]:
# let' write the dataset as Table in parquet format
pct_invest_2019.write.format("parquet").saveAsTable("pct_invest_2019_unbucketed")

In [0]:
# write the same dataset into another parquet file, but this time perform bucketing (create 15 buckets based on id) and also save as table
pct_invest_2019.write.format("parquet").bucketBy(15, "customer_id").sortBy("pct_investment_2019").saveAsTable("pct_invest_2019_bucketed")

In [0]:
%sql
SHOW TABLES

database tableName isTemporary default countries false default flights_data false default happiness_scores false default loan_data false default loan_data_females_under_30 false default olympics false default partitioned_loan_data_females_under_30 false default pct_invest_2019_bucketed false default pct_invest_2019_unbucketed false

In [0]:
%sql
SELECT * FROM pct_invest_2019_bucketed

customer_id pct_investment_2019 3394715 3.3500006213493805E-6 3925063 2.5082757760030994E-5 3616448 4.721477589331169E-5 3353138 1.0022960771494116E-4 3704865 1.1444282188599608E-4 3831339 1.2513462393792807E-4 3205115 1.3116886429109798E-4 3420937 1.7840825513182335E-4 3367163 1.8359268950907115E-4 3910888 1.963006651413135E-4 3163722 2.053060213662583E-4 3846293 2.238923138860871E-4 3710195 2.6296503071376875E-4 3310944 2.891548866533755E-4 3244897 3.03892709594078E-4 3326472 3.6468517943222256E-4 3048347 3.8112683515567625E-4 3373615 3.9727906364117604E-4 3121236 4.0533393807984375E-4 3261668 4.0641544354902415E-4 3055948 4.1080944903493233E-4 3992973 4.424956192254914E-4 3378841 4.5647190427200446E-4 3715195 4.730228942226855E-4 3540125 5.005169021823352E-4 3053567 5.438555527311761E-4 3173843 5.515729327799646E-4 3853993 5.533232160893631E-4 3568594 5.578454745933659E-4 3773463 5.585265933291117E-4 3303591 5.71430637728243E-4 3828690 5.827770173755242E-4 3046097 6.030255774244209E-4 3874239 6.17450922093421E-4 3623675 6.391484196905939E-4 3874364 6.530904251335068E-4 3821831 6.587448476599311E-4 3083088 7.202391555657384E-4 3740534 7.35838779525988E-4 3673123 7.632454792514398E-4 3499413 7.645004446601433E-4 3602829 7.729272433060208E-4 3201419 7.744316154654207E-4 3641867 7.784889431706743E-4 3541038 7.988301470345238E-4 3956715 8.033725451846996E-4 3056191 8.040807109159775E-4 3234919 8.069120889535597E-4 3027046 8.344260833704764E-4 3946002 8.511576516604391E-4 3399352 8.672027797050896E-4 3811365 8.705382604848877E-4 3066681 9.213330619449733E-4 3646697 9.416004117488441E-4 3993295 9.62194531410332E-4 3024993 0.001021510805660819 3417684 0.0010320455484886804 3512756 0.0010600928062832748 3136506 0.0010947992802639028 3766390 0.0011637751783741823 3711676 0.001192980765146734 3413187 0.0011945171070726346 3985327 0.0012012662810126917 3489175 0.0012132677855661855 3254343 0.0012266898414370342 3833488 0.001233894373364408 3548828 0.0012387932178034022 3481162 0.0012517164490299937 3822547 0.001261370888540836 3763893 0.001267103780581036 3119734 0.001270419616241636 3677031 0.0012915674296695157 3505683 0.0013114400188036779 3717279 0.0013232101510365357 3740802 0.001336734486079738 3387882 0.0013388810130191553 3238006 0.0013537372675700432 3268224 0.0013568413502893506 3682615 0.0013827709433207325 3424680 0.0013981396083169173 3711148 0.001418873967967138 3182267 0.0014194370961332359 3869246 0.0014563789490102952 3533224 0.0014920065757917378 3955125 0.0014950149748098607 3866520 0.0015062053975444245 3134407 0.0015202239883227442 3985583 0.0015330453861175375 3341523 0.0015368304128221544 3285715 0.0015498999098991773 3575098 0.001559302067339341 3976775 0.0015597293179260285 3523633 0.0015648064450662913 3579437 0.0015811357671968729 3866670 0.0016249712031123353 3892475 0.0016254080717111874 3125748 0.0016324460331931245 3228384 0.0016372926223394701 3015583 0.0016430771317160753 3775590 0.0016618588868313466 3228694 0.0016690362712132867 3152578 0.0016691847263664572 3474790 0.0016907837738975307 3398898 0.0016944586396459016 3803135 0.0017095510979692197 3351107 0.0017279691261231633 3793527 0.0017372483337759759 3880186 0.001741063471468851 3727295 0.0017446547507375954 3480711 0.0017815427189833422 3999869 0.0017861256445271811 3435031 0.001807222147883869 3204314 0.0018212260937029434 3382479 0.001829344606282035 3778006 0.0018625702536331223 3244642 0.0018635581251041922 3130185 0.0018721217678454583 3185942 0.0018749672145429441 3766441 0.0019116811757055041 3379875 0.0019324696295216492 3642117 0.0019395101944872373 3526755 0.0019495932789415082 3740165 0.0019679254059381535 3975287 0.001974061470088606 3986592 0.001981945341903102 3014497 0.0020003033133231263 3682574 0.002004221518737914 3886966 0.0020131798670393053 3427135 0.00202838305180586 3057533 0.0020385321558070713 3260995 0.00208147359836397 3693559 0.002084622691178817 3599668 0.0021005501309165897 3579620 0.002113776562716496 3586692 0.002

In [0]:
%sql
SELECT * FROM pct_invest_2019_unbucketed

customer_id pct_investment_2019 9000000 0.1709497137955568 9000001 0.8051143958005459 9000002 0.5775925576589018 9000003 0.9476047869880925 9000004 0.2093704977577 9000005 0.36664222617947817 9000006 0.8078688178371882 9000007 0.7135143433452461 9000008 0.7195325566306053 9000009 0.31335292311175456 9000010 0.8062503712025726 9000011 0.10814914646176654 9000012 0.3362232980701172 9000013 0.8133304803837667 9000014 0.47649428738170896 9000015 0.524728096293865 9000016 0.9701253460019921 9000017 0.6232167713919952 9000018 0.5089687568245219 9000019 0.5467504094508642 9000020 0.014097110603182639 9000021 0.6286498635045461 9000022 0.022170719725254195 9000023 0.7313372847411099 9000024 0.6822647942285944 9000025 0.09865667253909105 9000026 0.06622344831941485 9000027 0.5076232741953021 9000028 0.19412650105821194 9000029 0.7196252950914184 9000030 0.4309638186000935 9000031 0.6606700902936103 9000032 0.9980781298103227 9000033 0.6993604281994343 9000034 0.3621992720262205 9000035 0.9821302776190866 9000036 0.5709739789775365 9000037 0.6038715879276334 9000038 0.9135015594663367 9000039 0.9152393673348903 9000040 0.5601961495594829 9000041 0.5030522433081416 9000042 0.03880069884212001 9000043 0.1598957316573555 9000044 0.08497597715570515 9000045 0.6928023036324205 9000046 0.28203421912882276 9000047 0.050674455913206295 9000048 0.6110517824163579 9000049 0.5266503226482994 9000050 0.5514494213111066 9000051 0.06499743068716202 9000052 0.8203715556624479 9000053 0.8609641258077847 9000054 0.2728398229224983 9000055 0.9100370293723855 9000056 0.8846536356755017 9000057 0.08969927916746101 9000058 0.6524612555635354 9000059 0.23786282971749773 9000060 0.5352770539384141 9000061 0.12153481344756023 9000062 0.5771966653256273 9000063 0.8092021738191977 9000064 0.7766956595922987 9000065 0.7208508032377924 9000066 0.9317976052287359 9000067 0.032045981121342604 9000068 0.920360496706323 9000069 0.836098898121259 9000070 0.19885041687259075 9000071 0.9207416019290241 9000072 0.32046689536810846 9000073 0.48400888350347815 9000074 0.5411403350083326 9000075 0.382195051568918 9000076 0.2670434277204943 9000077 0.8447323655410356 9000078 0.32138034039414365 9000079 0.32028152351184735 9000080 0.9352700536348454 9000081 0.05984926325784168 9000082 0.47415236401346694 9000083 0.7729978001849526 9000084 0.4366856060233195 9000085 0.8875227420980584 9000086 0.6657157882395947 9000087 0.28336233795831234 9000088 0.8662913634047689 9000089 0.7326515162751059 9000090 0.6180359375451097 9000091 0.7195975867438303 9000092 0.2089478851660026 9000093 0.044272314352424735 9000094 0.4353368227701675 9000095 0.5725975885697011 9000096 0.7338905477986692 9000097 0.4068076515936745 9000098 0.7979003735415908 9000099 0.7546308964312055 9000100 0.7108488196666733 9000101 0.5233999588913362 9000102 0.6741722950024432 9000103 0.7498121366602603 9000104 0.38885504858564235 9000105 0.4011342256875613 9000106 0.17083643273868143 9000107 0.002505600522091034 9000108 0.5790050039811174 9000109 0.39791120619607256 9000110 0.7143172757060233 9000111 0.05873493578779232 9000112 0.9374992261322597 9000113 0.38703667779835316 9000114 0.9087820885752338 9000115 0.1766832320256463 9000116 0.22300562818494019 9000117 0.8501958177682462 9000118 0.03182480437026247 9000119 0.5149909139265693 9000120 0.036806723491295434 9000121 0.03793669696983093 9000122 0.04874687194318261 9000123 0.7702378879843016 9000124 0.7086532984353837 9000125 0.6898233942264838 9000126 0.19743042647116593 9000127 0.1792424140958192 9000128 0.5539100294060335 9000129 0.6026282217154758 9000130 0.4936380573971677 9000131 0.04511033790134866 9000132 0.1507916359289413 9000133 0.8141961405828485 9000134 0.5540701243797089 9000135 0.05027016568414355 9000136 0.6926474011711525 9000137 0.18446051178851508 9000138 0.40938072629838673 9000139 0.22393800050758073 9000140 0.10747560436994164 9000141 0.17396023627676482 9000142 0.8098946669087561 9000143 0.036558200090541004 9000144 0.4717201693605697 90001

In [0]:
%sql 
SELECT min(customer_id), max(customer_id) FROM pct_invest_2019_unbucketed

min(customer_id) max(customer_id) 1 14999999

In [0]:
%sql 
SELECT min(pct_investment_2019), max(pct_investment_2019) FROM pct_invest_2019_unbucketed

min(pct_investment_2019) max(pct_investment_2019) 1.3972530576999986E-8 0.9999999933863358

In [0]:
# Lets create another table with pct_investment in 2020
pct_invest_2020 = customer_id.select(col("id").alias("customer_id"), rand(2).alias("pct_investment_2020"))

display(pct_invest_2020)

customer_id pct_investment_2020 1 0.5311207224659675 2 0.2861372051669987 3 0.49443063728956627 4 0.45537077449713226 5 0.8792399632068049 6 0.3644632675391507 7 0.45019682421810947 8 0.4199726628902539 9 0.7051587870577706 10 0.015088145878069947 11 0.5603832248407625 12 0.2609884611090595 13 0.2066778320568361 14 0.15479335724602938 15 0.8522642178101167 16 0.09126135418182602 17 0.7797069626164488 18 0.4827730566954318 19 0.1334859258635921 20 0.4593032815678898 21 0.7294241219316996 22 0.4251863711399191 23 0.09518369613022148 24 0.5307438792841394 25 0.42451309444944985 26 0.6410189886731019 27 0.9353348235075628 28 0.6284220367428787 29 0.047063476847890695 30 0.9085408738709839 31 0.4991963923361348 32 0.4330773873736192 33 0.82500868558683 34 0.7803560017713331 35 0.5858104716299906 36 0.8571131722179952 37 0.2654136270104065 38 0.1716270321198896 39 0.34480590238362896 40 0.676654569532795 41 0.9812699525016548 42 0.8600796510405562 43 0.30555563208280156 44 0.6688701155355138 45 0.578175574678228 46 0.9980921624111733 47 0.30022651923821997 48 0.10865022684833947 49 0.7676492234264799 50 0.21563769370742636 51 0.11300607530903006 52 0.4009301054493236 53 0.9811282871027304 54 0.2688121716080083 55 0.5862885467270194 56 0.36096224410736966 57 0.5436959489545153 58 0.6409222026959259 59 0.9024901090126016 60 0.16490580113314113 61 0.1903256880309515 62 0.6357544843418271 63 0.9409547568198007 64 0.23269885063578455 65 0.19693438659970564 66 0.5073932248633354 67 0.3976371778868273 68 0.12805705758657981 69 0.7539269974025733 70 0.32222322365803413 71 0.7893272343070601 72 0.9069011618954111 73 0.3975524747667898 74 0.020978623889554515 75 0.9908441965936985 76 0.7272341175438437 77 0.03227227777913466 78 0.018803794876566138 79 0.4817137191135501 80 0.990574198197933 81 0.5984063566410971 82 0.30543669628556314 83 0.19785869253328625 84 0.10942107087028785 85 0.899170224502107 86 0.6330704892986039 87 0.6996651850975388 88 0.7853219782377372 89 0.08817450139773364 90 0.6317645103183595 91 0.917651338135916 92 0.2750790124432496 93 0.4943132966493643 94 0.006161857487885114 95 0.24737454251826285 96 0.9718630614544266 97 0.6154000178473078 98 0.07611105094972959 99 0.8795719628044084 100 0.4999963980146014 101 0.21480182113948632 102 0.29745043742966915 103 0.1921043789798078 104 0.12686499562152054 105 0.16236646128547916 106 0.15657823021279882 107 0.017366683093678392 108 0.5929512604874848 109 0.3774536989473759 110 0.2902847579929241 111 0.017897449117095898 112 0.7847751699872278 113 0.07890327647501483 114 0.8216623128854313 115 0.3995578095594451 116 0.5474627439252697 117 0.93465124219285 118 0.41889493748393225 119 0.6270233206594646 120 0.6847381660344631 121 0.3133900034705358 122 0.09593080173514801 123 0.1884219435268566 124 0.4389946998747474 125 0.15087881363980704 126 0.8370923529871792 127 0.3317541605231751 128 0.813231187986123 129 0.307219625765905 130 0.05758307421363118 131 0.49919112411081434 132 0.14569946308983106 133 0.9619487464810839 134 0.3271217691218261 135 0.6995256664088217 136 0.8051849962070459 137 0.03092625372955371 138 0.8569953869891824 139 0.11440592299265329 140 0.7123130956674699 141 0.5376777604596246 142 0.08176433940912853 143 0.6723532613649085 144 0.26937684306261367 145 0.6668311854003359 146 0.8736484858345149 147 0.10188026525142313 148 0.8206723867477947 149 0.07833030135433505 150 0.5870413378193649 151 0.43597136333737474 152 0.08987582015514561 153 0.24855110845342476 154 0.2622458884524199 155 0.03321593537073175 156 0.27874174422498055 157 0.943440294722742 158 0.839180638196066 159 0.35711812939631693 160 0.14503748827859642 161 0.7211523729105186 162 0.4663449565826633 163 0.6064469726646279 164 0.7348036566036469 165 0.897994381255742 166 0.6575907439844872 167 0.868458735866441 168 0.8254057933050021 169 0.8079813970499058 170 0.5324119287675848 171 0.777222343753848 172 0.04699460829768887 173 0.8716441212362908 174 0.5484494386272858 175 0.10930102108669348 

In [0]:
pct_invest_2020.write.format("parquet").bucketBy(15, "customer_id").sortBy("pct_investment_2020").saveAsTable("pct_invest_2020_bucketed")

In [0]:
%sql
SHOW TABLES

database tableName isTemporary default countries false default flights_data false default happiness_scores false default loan_data false default loan_data_females_under_30 false default olympics false default partitioned_loan_data_females_under_30 false default pct_invest_2019_bucketed false default pct_invest_2019_unbucketed false default pct_invest_2020_bucketed false

In [0]:
# Read from tables into new spark tables
pct_2019_unbucketed = spark.table("pct_invest_2019_unbucketed")
pct_2019_bucketed = spark.table("pct_invest_2019_bucketed")
pct_2020_bucketed = spark.table("pct_invest_2020_bucketed")

In [0]:
# perform join on unbucketed and bucketed tables (both have to be repartitioned and shuffled in process)
pct_2019_unbucketed.join(pct_2020_bucketed, "customer_id").explain()

== Physical Plan ==
AdaptiveSparkPlan isFinalPlan=false
+- Project [customer_id#77443L, pct_investment_2019#77444, pct_investment_2020#77542]
 +- SortMergeJoin [customer_id#77443L], [customer_id#77541L], Inner
 :- Sort [customer_id#77443L ASC NULLS FIRST], false, 0
 : +- Exchange hashpartitioning(customer_id#77443L, 15), ENSURE_REQUIREMENTS, [id=#26963]
 : +- Filter isnotnull(customer_id#77443L)
 : +- FileScan parquet default.pct_invest_2019_unbucketed[customer_id#77443L,pct_investment_2019#77444] Batched: true, DataFilters: [isnotnull(customer_id#77443L)], Format: Parquet, Location: InMemoryFileIndex(1 paths)[dbfs:/user/hive/warehouse/pct_invest_2019_unbucketed], PartitionFilters: [], PushedFilters: [IsNotNull(customer_id)], ReadSchema: struct<customer_id:bigint,pct_investment_2019:double>
 +- Sort [customer_id#77541L ASC NULLS FIRST], false, 0
 +- Filter isnotnull(customer_id#77541L)
 +- FileScan parquet default.pct_invest_2020_bucketed[customer_id#77541L,pct_investment_2020#77542] Batched: true, Bucketed: true, DataFilters: [isnotnull(customer_id#77541L)], Format: Parquet, Location: InMemoryFileIndex(1 paths)[dbfs:/user/hive/warehouse/pct_invest_2020_bucketed], PartitionFilters: [], PushedFilters: [IsNotNull(customer_id)], ReadSchema: struct<customer_id:bigint,pct_investment_2020:double>, SelectedBucketsCount: 15 out of 15

In [0]:
display(pct_2019_unbucketed.join(pct_2020_bucketed, "customer_id"))

customer_id pct_investment_2019 pct_investment_2020 6 0.7167704217972344 0.3644632675391507 16 0.9643107647469807 0.09126135418182602 63 0.2970280250906274 0.9409547568198007 64 0.3992368306476186 0.23269885063578455 70 0.2519628438595569 0.32222322365803413 80 0.10019565652162143 0.990574198197933 123 0.06444107879131655 0.1884219435268566 130 0.942723722436596 0.05758307421363118 148 0.7218504473666008 0.8206723867477947 163 0.5427676535722059 0.6064469726646279 177 0.9336899341841564 0.03684699338744102 195 0.9983629267462243 0.8492044317979779 207 0.8704096309337637 0.43058818288971556 259 0.22736308032122843 0.18652146383543777 276 0.4605483223680942 0.9747049873169042 277 9.867199591546694E-4 0.191994398161353 280 0.9827759141871294 0.62446256949589 303 0.8334289202276002 0.40765464077250557 312 0.9575070160008401 0.1449814891613037 342 0.7009540066288226 0.34485662012757246 345 0.5210178023338528 0.5710969219881701 346 0.7031336272814424 0.45782399885503056 362 0.8831321939091832 0.6544556469855634 366 0.6939716943213781 0.5497035086975326 389 0.8264354974436313 0.5729596409240348 394 0.6290242611852669 0.31411287570747914 410 0.7976129106898335 0.8823454041907304 425 0.12557515655256823 0.3711760418204276 427 0.10071861345017286 0.8738257376609904 436 0.4255715409063232 0.3724435418412304 447 0.23990895202453133 0.7132111638246191 449 0.5576071103073809 0.9143419533711583 450 0.8960262295244534 0.3794304596005924 467 0.12358043325767554 0.8160611558993154 480 0.8303778147713129 0.5750153836763784 484 0.5263385334490036 0.3769985943315465 486 0.4146815065475128 0.7128145379319163 488 0.9447096491456741 0.7142867156723384 498 0.2934655259414589 0.7147593666104087 501 0.09200754145440515 0.8432822340971081 504 0.9216990728226659 0.7317257576502676 549 0.20547639768891612 0.70373983431738 572 0.5479290583342901 0.4898039785032151 595 0.17364700511626907 0.11621702501609488 603 0.5431552710500879 0.4106242050731753 619 0.11411909159770461 0.5184785399897149 636 0.6512419299203452 0.49791409638677997 643 0.4306927528816421 0.3495499156311892 650 0.7223150741790226 0.9523164479066951 664 0.10166166689700906 0.37767158408154167 679 0.9760562914626946 0.8499113682307876 683 0.8197393336879911 0.3883379066088285 752 0.5400014010099138 0.369872114924533 754 0.3882303126437364 0.8106639057647583 774 0.7394907967976531 0.5731922639149015 847 0.8490449088674427 0.8530401964708061 848 0.5449320977856051 0.2679317040710054 852 0.3515533176661749 0.9342280436560231 866 0.9078655257599755 0.27232295048273325 870 0.5853513787786511 0.6818177388433184 872 0.01105373195671655 0.10747494236855692 889 0.604477160376489 0.47079657544281794 893 0.10088812866891039 0.13413373563670306 894 0.49197316422616144 0.37456357712158095 906 0.16614386736846076 0.7601162888141194 932 0.3233126421156751 0.798853914877384 951 0.0288509572991541 0.7816076418568833 959 0.17370979528320496 0.4143794220462609 964 0.896007891594797 0.6523305651063305 1011 0.8558277600960008 0.2561881794346722 1022 0.5194150005942777 0.34152619032954 1024 0.7267146519239475 0.7824337453842027 1051 0.11407528789246557 0.7777990806446168 1059 0.5808926137094264 0.9127017922544161 1077 0.9313296226145618 0.6210580128947677 1081 0.3289663447745951 0.26555960737865836 1102 0.9569416515119329 0.8505822667833036 1104 0.18819800119577157 0.4667369773125374 1119 0.3375138967883551 0.32092922814753344 1131 0.389759109082087 0.18846751643989157 1177 0.9861912275269126 0.7587996227875681 1185 0.6312277818785499 0.9366870287259402 1188 0.09876743717319336 0.9052776320288338 1193 0.5691792043998768 0.7296671119816943 1231 0.45975199001337597 0.5690728479204314 1242 0.7639718035083176 0.6614842932105178 1250 0.7334359065258128 0.7674571975713829 1265 0.5589831451947933 0.31299560764058454 1306 0.46138956130400044 0.7710904020488571 1307 0.023166862465855642 0.48634905563504105 1321 0.8871266930155389 0.6740985664868007 1328 0.6395570014615864 0.8724086217058131 1357 0.6122880830365242 0.604408

In [0]:
# perform repartitioning that corresponds to the number of buckets. Now repartition and shuffling runs just on unbucketed table
pct_2019_unbucketed.repartition(15, "customer_id").join(pct_2020_bucketed, "customer_id").explain()

== Physical Plan ==
AdaptiveSparkPlan isFinalPlan=false
+- Project [customer_id#77443L, pct_investment_2019#77444, pct_investment_2020#77542]
 +- SortMergeJoin [customer_id#77443L], [customer_id#77541L], Inner
 :- Sort [customer_id#77443L ASC NULLS FIRST], false, 0
 : +- Exchange hashpartitioning(customer_id#77443L, 15), REPARTITION_BY_NUM, [id=#27201]
 : +- Filter isnotnull(customer_id#77443L)
 : +- FileScan parquet default.pct_invest_2019_unbucketed[customer_id#77443L,pct_investment_2019#77444] Batched: true, DataFilters: [isnotnull(customer_id#77443L)], Format: Parquet, Location: InMemoryFileIndex(1 paths)[dbfs:/user/hive/warehouse/pct_invest_2019_unbucketed], PartitionFilters: [], PushedFilters: [IsNotNull(customer_id)], ReadSchema: struct<customer_id:bigint,pct_investment_2019:double>
 +- Sort [customer_id#77541L ASC NULLS FIRST], false, 0
 +- Filter isnotnull(customer_id#77541L)
 +- FileScan parquet default.pct_invest_2020_bucketed[customer_id#77541L,pct_investment_2020#77542] Batched: true, Bucketed: true, DataFilters: [isnotnull(customer_id#77541L)], Format: Parquet, Location: InMemoryFileIndex(1 paths)[dbfs:/user/hive/warehouse/pct_invest_2020_bucketed], PartitionFilters: [], PushedFilters: [IsNotNull(customer_id)], ReadSchema: struct<customer_id:bigint,pct_investment_2020:double>, SelectedBucketsCount: 15 out of 15

In [0]:
display(pct_2019_unbucketed.repartition(15, "customer_id").join(pct_2020_bucketed, "customer_id"))

customer_id pct_investment_2019 pct_investment_2020 6 0.7167704217972344 0.3644632675391507 16 0.9643107647469807 0.09126135418182602 63 0.2970280250906274 0.9409547568198007 64 0.3992368306476186 0.23269885063578455 70 0.2519628438595569 0.32222322365803413 80 0.10019565652162143 0.990574198197933 123 0.06444107879131655 0.1884219435268566 130 0.942723722436596 0.05758307421363118 148 0.7218504473666008 0.8206723867477947 163 0.5427676535722059 0.6064469726646279 177 0.9336899341841564 0.03684699338744102 195 0.9983629267462243 0.8492044317979779 207 0.8704096309337637 0.43058818288971556 259 0.22736308032122843 0.18652146383543777 276 0.4605483223680942 0.9747049873169042 277 9.867199591546694E-4 0.191994398161353 280 0.9827759141871294 0.62446256949589 303 0.8334289202276002 0.40765464077250557 312 0.9575070160008401 0.1449814891613037 342 0.7009540066288226 0.34485662012757246 345 0.5210178023338528 0.5710969219881701 346 0.7031336272814424 0.45782399885503056 362 0.8831321939091832 0.6544556469855634 366 0.6939716943213781 0.5497035086975326 389 0.8264354974436313 0.5729596409240348 394 0.6290242611852669 0.31411287570747914 410 0.7976129106898335 0.8823454041907304 425 0.12557515655256823 0.3711760418204276 427 0.10071861345017286 0.8738257376609904 436 0.4255715409063232 0.3724435418412304 447 0.23990895202453133 0.7132111638246191 449 0.5576071103073809 0.9143419533711583 450 0.8960262295244534 0.3794304596005924 467 0.12358043325767554 0.8160611558993154 480 0.8303778147713129 0.5750153836763784 484 0.5263385334490036 0.3769985943315465 486 0.4146815065475128 0.7128145379319163 488 0.9447096491456741 0.7142867156723384 498 0.2934655259414589 0.7147593666104087 501 0.09200754145440515 0.8432822340971081 504 0.9216990728226659 0.7317257576502676 549 0.20547639768891612 0.70373983431738 572 0.5479290583342901 0.4898039785032151 595 0.17364700511626907 0.11621702501609488 603 0.5431552710500879 0.4106242050731753 619 0.11411909159770461 0.5184785399897149 636 0.6512419299203452 0.49791409638677997 643 0.4306927528816421 0.3495499156311892 650 0.7223150741790226 0.9523164479066951 664 0.10166166689700906 0.37767158408154167 679 0.9760562914626946 0.8499113682307876 683 0.8197393336879911 0.3883379066088285 752 0.5400014010099138 0.369872114924533 754 0.3882303126437364 0.8106639057647583 774 0.7394907967976531 0.5731922639149015 847 0.8490449088674427 0.8530401964708061 848 0.5449320977856051 0.2679317040710054 852 0.3515533176661749 0.9342280436560231 866 0.9078655257599755 0.27232295048273325 870 0.5853513787786511 0.6818177388433184 872 0.01105373195671655 0.10747494236855692 889 0.604477160376489 0.47079657544281794 893 0.10088812866891039 0.13413373563670306 894 0.49197316422616144 0.37456357712158095 906 0.16614386736846076 0.7601162888141194 932 0.3233126421156751 0.798853914877384 951 0.0288509572991541 0.7816076418568833 959 0.17370979528320496 0.4143794220462609 964 0.896007891594797 0.6523305651063305 1011 0.8558277600960008 0.2561881794346722 1022 0.5194150005942777 0.34152619032954 1024 0.7267146519239475 0.7824337453842027 1051 0.11407528789246557 0.7777990806446168 1059 0.5808926137094264 0.9127017922544161 1077 0.9313296226145618 0.6210580128947677 1081 0.3289663447745951 0.26555960737865836 1102 0.9569416515119329 0.8505822667833036 1104 0.18819800119577157 0.4667369773125374 1119 0.3375138967883551 0.32092922814753344 1131 0.389759109082087 0.18846751643989157 1177 0.9861912275269126 0.7587996227875681 1185 0.6312277818785499 0.9366870287259402 1188 0.09876743717319336 0.9052776320288338 1193 0.5691792043998768 0.7296671119816943 1231 0.45975199001337597 0.5690728479204314 1242 0.7639718035083176 0.6614842932105178 1250 0.7334359065258128 0.7674571975713829 1265 0.5589831451947933 0.31299560764058454 1306 0.46138956130400044 0.7710904020488571 1307 0.023166862465855642 0.48634905563504105 1321 0.8871266930155389 0.6740985664868007 1328 0.6395570014615864 0.8724086217058131 1357 0.6122880830365242 0.604408

In [0]:
# perform another repartitioning (without specifying number of partitions)
pct_2019_unbucketed.repartition("customer_id").join(pct_2020_bucketed, "customer_id").explain()

== Physical Plan ==
AdaptiveSparkPlan isFinalPlan=false
+- Project [customer_id#77443L, pct_investment_2019#77444, pct_investment_2020#77542]
 +- SortMergeJoin [customer_id#77443L], [customer_id#77541L], Inner
 :- Sort [customer_id#77443L ASC NULLS FIRST], false, 0
 : +- Exchange hashpartitioning(customer_id#77443L, 15), REPARTITION_BY_COL, [id=#27455]
 : +- Filter isnotnull(customer_id#77443L)
 : +- FileScan parquet default.pct_invest_2019_unbucketed[customer_id#77443L,pct_investment_2019#77444] Batched: true, DataFilters: [isnotnull(customer_id#77443L)], Format: Parquet, Location: InMemoryFileIndex(1 paths)[dbfs:/user/hive/warehouse/pct_invest_2019_unbucketed], PartitionFilters: [], PushedFilters: [IsNotNull(customer_id)], ReadSchema: struct<customer_id:bigint,pct_investment_2019:double>
 +- Sort [customer_id#77541L ASC NULLS FIRST], false, 0
 +- Filter isnotnull(customer_id#77541L)
 +- FileScan parquet default.pct_invest_2020_bucketed[customer_id#77541L,pct_investment_2020#77542] Batched: true, Bucketed: true, DataFilters: [isnotnull(customer_id#77541L)], Format: Parquet, Location: InMemoryFileIndex(1 paths)[dbfs:/user/hive/warehouse/pct_invest_2020_bucketed], PartitionFilters: [], PushedFilters: [IsNotNull(customer_id)], ReadSchema: struct<customer_id:bigint,pct_investment_2020:double>, SelectedBucketsCount: 15 out of 15

In [0]:
# in this query no repartitions and shuffles will be performed at all
pct_2019_bucketed.join(pct_2020_bucketed, "customer_id").explain()

== Physical Plan ==
AdaptiveSparkPlan isFinalPlan=false
+- Project [customer_id#77433L, pct_investment_2019#77434, pct_investment_2020#77542]
 +- SortMergeJoin [customer_id#77433L], [customer_id#77541L], Inner
 :- Sort [customer_id#77433L ASC NULLS FIRST], false, 0
 : +- Filter isnotnull(customer_id#77433L)
 : +- FileScan parquet default.pct_invest_2019_bucketed[customer_id#77433L,pct_investment_2019#77434] Batched: true, Bucketed: true, DataFilters: [isnotnull(customer_id#77433L)], Format: Parquet, Location: InMemoryFileIndex(1 paths)[dbfs:/user/hive/warehouse/pct_invest_2019_bucketed], PartitionFilters: [], PushedFilters: [IsNotNull(customer_id)], ReadSchema: struct<customer_id:bigint,pct_investment_2019:double>, SelectedBucketsCount: 15 out of 15
 +- Sort [customer_id#77541L ASC NULLS FIRST], false, 0
 +- Filter isnotnull(customer_id#77541L)
 +- FileScan parquet default.pct_invest_2020_bucketed[customer_id#77541L,pct_investment_2020#77542] Batched: true, Bucketed: true, DataFilters: [isnotnull(customer_id#77541L)], Format: Parquet, Location: InMemoryFileIndex(1 paths)[dbfs:/user/hive/warehouse/pct_invest_2020_bucketed], PartitionFilters: [], PushedFilters: [IsNotNull(customer_id)], ReadSchema: struct<customer_id:bigint,pct_investment_2020:double>, SelectedBucketsCount: 15 out of 15

In [0]:
display(pct_2019_bucketed.join(pct_2020_bucketed, "customer_id"))

customer_id pct_investment_2019 pct_investment_2020 6 0.7167704217972344 0.3644632675391507 16 0.9643107647469807 0.09126135418182602 63 0.2970280250906274 0.9409547568198007 64 0.3992368306476186 0.23269885063578455 70 0.2519628438595569 0.32222322365803413 80 0.10019565652162143 0.990574198197933 123 0.06444107879131655 0.1884219435268566 130 0.942723722436596 0.05758307421363118 148 0.7218504473666008 0.8206723867477947 163 0.5427676535722059 0.6064469726646279 177 0.9336899341841564 0.03684699338744102 195 0.9983629267462243 0.8492044317979779 207 0.8704096309337637 0.43058818288971556 259 0.22736308032122843 0.18652146383543777 276 0.4605483223680942 0.9747049873169042 277 9.867199591546694E-4 0.191994398161353 280 0.9827759141871294 0.62446256949589 303 0.8334289202276002 0.40765464077250557 312 0.9575070160008401 0.1449814891613037 342 0.7009540066288226 0.34485662012757246 345 0.5210178023338528 0.5710969219881701 346 0.7031336272814424 0.45782399885503056 362 0.8831321939091832 0.6544556469855634 366 0.6939716943213781 0.5497035086975326 389 0.8264354974436313 0.5729596409240348 394 0.6290242611852669 0.31411287570747914 410 0.7976129106898335 0.8823454041907304 425 0.12557515655256823 0.3711760418204276 427 0.10071861345017286 0.8738257376609904 436 0.4255715409063232 0.3724435418412304 447 0.23990895202453133 0.7132111638246191 449 0.5576071103073809 0.9143419533711583 450 0.8960262295244534 0.3794304596005924 467 0.12358043325767554 0.8160611558993154 480 0.8303778147713129 0.5750153836763784 484 0.5263385334490036 0.3769985943315465 486 0.4146815065475128 0.7128145379319163 488 0.9447096491456741 0.7142867156723384 498 0.2934655259414589 0.7147593666104087 501 0.09200754145440515 0.8432822340971081 504 0.9216990728226659 0.7317257576502676 549 0.20547639768891612 0.70373983431738 572 0.5479290583342901 0.4898039785032151 595 0.17364700511626907 0.11621702501609488 603 0.5431552710500879 0.4106242050731753 619 0.11411909159770461 0.5184785399897149 636 0.6512419299203452 0.49791409638677997 643 0.4306927528816421 0.3495499156311892 650 0.7223150741790226 0.9523164479066951 664 0.10166166689700906 0.37767158408154167 679 0.9760562914626946 0.8499113682307876 683 0.8197393336879911 0.3883379066088285 752 0.5400014010099138 0.369872114924533 754 0.3882303126437364 0.8106639057647583 774 0.7394907967976531 0.5731922639149015 847 0.8490449088674427 0.8530401964708061 848 0.5449320977856051 0.2679317040710054 852 0.3515533176661749 0.9342280436560231 866 0.9078655257599755 0.27232295048273325 870 0.5853513787786511 0.6818177388433184 872 0.01105373195671655 0.10747494236855692 889 0.604477160376489 0.47079657544281794 893 0.10088812866891039 0.13413373563670306 894 0.49197316422616144 0.37456357712158095 906 0.16614386736846076 0.7601162888141194 932 0.3233126421156751 0.798853914877384 951 0.0288509572991541 0.7816076418568833 959 0.17370979528320496 0.4143794220462609 964 0.896007891594797 0.6523305651063305 1011 0.8558277600960008 0.2561881794346722 1022 0.5194150005942777 0.34152619032954 1024 0.7267146519239475 0.7824337453842027 1051 0.11407528789246557 0.7777990806446168 1059 0.5808926137094264 0.9127017922544161 1077 0.9313296226145618 0.6210580128947677 1081 0.3289663447745951 0.26555960737865836 1102 0.9569416515119329 0.8505822667833036 1104 0.18819800119577157 0.4667369773125374 1119 0.3375138967883551 0.32092922814753344 1131 0.389759109082087 0.18846751643989157 1177 0.9861912275269126 0.7587996227875681 1185 0.6312277818785499 0.9366870287259402 1188 0.09876743717319336 0.9052776320288338 1193 0.5691792043998768 0.7296671119816943 1231 0.45975199001337597 0.5690728479204314 1242 0.7639718035083176 0.6614842932105178 1250 0.7334359065258128 0.7674571975713829 1265 0.5589831451947933 0.31299560764058454 1306 0.46138956130400044 0.7710904020488571 1307 0.023166862465855642 0.48634905563504105 1321 0.8871266930155389 0.6740985664868007 1328 0.6395570014615864 0.8724086217058131 1357 0.6122880830365242 0.604408